In [1]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
from IPython.display import display
from bokeh.io import output_file, show, output_notebook,push_notebook
from bokeh.models import ColumnDataSource, HoverTool
from bokeh.plotting import figure
from bokeh.layouts import gridplot
from ipywidgets import interact_manual

import sys
import warnings
if not sys.warnoptions:
    warnings.simplefilter("ignore")
    
output_notebook()

def tanh(x):
    return  -1.0 + 2.0 / (1.0 + np.exp(-x))

df1=pd.read_csv('NYU_XAU_USD_20142015.csv',index_col=1)
df2=pd.read_csv('NYU_USD_JPY_2016.csv',index_col=1)

df1.index=pd.to_datetime(df1.index)
df2.index=pd.to_datetime(df2.index)
df1=df1.drop(columns='Ticker')
df2=df2.drop(columns='Ticker')
df1['Return']=df1['Price']/df1['Price'].shift(1)-1
df2['Return']=df2['Price'].pct_change()
spd=0/10000

Loading BokehJS ...

momentum strategy with two protection: Flow protection and tanh protection

In [2]:

XAU_OutS=df1.iloc[int(2*df1.shape[0]/3)+1:,:]
XAU_InS=df1.iloc[:int(2*df1.shape[0]/3),:]

XAU_InS['Signal']=XAU_InS['Return'].rolling(24*7).sum()
XAU_InS['Signal']=XAU_InS['Signal']-(XAU_InS['Flow']-1.7)
XAU_InS['Signal']=XAU_InS['Signal'].apply(tanh)

XAU_InS['QS_R_NoFrac']=XAU_InS['Signal'].shift(1)*XAU_InS['Return']
XAU_InS['Delta_Signal']=XAU_InS['Signal']-XAU_InS['Signal'].shift(1)
XAU_InS['QS_R']=XAU_InS['QS_R_NoFrac']-XAU_InS['Delta_Signal'].abs()*(1+XAU_InS['Return'])*spd/2
XAU_InS['QS_R']=XAU_InS['QS_R'].fillna(0)

XAU_InS['Agg_QS_R']=(XAU_InS['QS_R']+1).cumprod()
XAU_InS['Agg_QS_R_NoFrac']=(XAU_InS['QS_R_NoFrac']+1).cumprod()

XAU_OutS['Signal']=XAU_OutS['Return'].rolling(24*7).sum()
XAU_OutS['Signal']=XAU_OutS['Signal']-(XAU_OutS['Flow']-1.7)
XAU_OutS['Signal']=XAU_OutS['Signal'].apply(tanh)

XAU_OutS['QS_R_NoFrac']=XAU_OutS['Signal'].shift(1)*XAU_OutS['Return']
XAU_OutS['Delta_Signal']=XAU_OutS['Signal']-XAU_OutS['Signal'].shift(1)
XAU_OutS['QS_R']=XAU_OutS['QS_R_NoFrac']-XAU_OutS['Delta_Signal'].abs()*(1+XAU_OutS['Return'])*spd/2
XAU_OutS['QS_R']=XAU_OutS['QS_R'].fillna(0)

XAU_OutS['Agg_QS_R']=(XAU_OutS['QS_R']+1).cumprod()
XAU_OutS['Agg_QS_R_NoFrac']=(XAU_OutS['QS_R_NoFrac']+1).cumprod()



In [3]:
JPY_OutS=df2.iloc[int(2*df2.shape[0]/3)+1:,:]
JPY_InS=df2.iloc[:int(2*df2.shape[0]/3),:]

JPY_InS['Signal']=JPY_InS['Return'].rolling(24*7).sum()
JPY_InS['Signal']=JPY_InS['Signal']-(JPY_InS['Flow']-1.4)
JPY_InS['Signal']=JPY_InS['Signal'].apply(tanh)

JPY_InS['QS_R_NoFrac']=JPY_InS['Signal'].shift(1)*JPY_InS['Return']
JPY_InS['Delta_Signal']=JPY_InS['Signal']-JPY_InS['Signal'].shift(1)
JPY_InS['QS_R']=JPY_InS['QS_R_NoFrac']-JPY_InS['Delta_Signal'].abs()*(1+JPY_InS['Return'])*spd/2
JPY_InS['QS_R']=JPY_InS['QS_R'].fillna(0)

JPY_InS['Agg_QS_R']=(JPY_InS['QS_R']+1).cumprod()
JPY_InS['Agg_QS_R_NoFrac']=(JPY_InS['QS_R_NoFrac']+1).cumprod()



JPY_OutS['Signal']=JPY_OutS['Return'].rolling(24*7).sum()
JPY_OutS['Signal']=JPY_OutS['Signal']-(JPY_OutS['Flow']-1.4)
JPY_OutS['Signal']=JPY_OutS['Signal'].apply(tanh)

JPY_OutS['QS_R_NoFrac']=JPY_OutS['Signal'].shift(1)*JPY_OutS['Return']
JPY_OutS['Delta_Signal']=JPY_OutS['Signal']-JPY_OutS['Signal'].shift(1)
JPY_OutS['QS_R']=JPY_OutS['QS_R_NoFrac']-JPY_OutS['Delta_Signal'].abs()*(1+JPY_OutS['Return'])*spd/2
JPY_OutS['QS_R']=JPY_OutS['QS_R'].fillna(0)

JPY_OutS['Agg_QS_R']=(JPY_OutS['QS_R']+1).cumprod()
JPY_OutS['Agg_QS_R_NoFrac']=(JPY_OutS['QS_R_NoFrac']+1).cumprod()


In [5]:
Performance_Stats=pd.DataFrame()

datalist = [XAU_InS, XAU_OutS, JPY_InS, JPY_OutS]
annual_ret = [] # annualized return
annual_vol = [] # annualized volatility
IR = []     # information ratio
largest_drawdown = []   # largest drawdown
yearret_largestDD = []  # yearly return/largest drawdown
winner_pct = []      # winner percentage
var99daily = []       # 99% hourly VAR
var95daily = []       # 95% hourly VAR
for i in range(4):
    annual_ret.append(pow(datalist[i]['Agg_QS_R'][-1], 255*24/datalist[i]['Agg_QS_R'].count()) - 1)
    annual_vol.append(datalist[i]['QS_R'].std()*np.sqrt(255*24))
    IR.append(annual_ret[i]/annual_vol[i])
    largest_drawdown.append((datalist[i]['Agg_QS_R'].cummax() - datalist[i]['Agg_QS_R']).max())
    winner_pct.append(datalist[i]['QS_R'][datalist[i]['QS_R'] > 0].count()/datalist[i]['QS_R'].count())
    yearret_largestDD.append(annual_ret[i]/largest_drawdown[i])
    daily_return = datalist[i].resample('d').last().dropna(subset=['Price'])
    var99daily.append(daily_return['QS_R'].quantile(.01)*100)
    var95daily.append(daily_return['QS_R'].quantile(.05)*100)
    
Performance_Stats=pd.DataFrame({'Annual Return(%)':annual_ret, 'Annual Volatility(%)':annual_vol, 'InfoRatio':IR, 'Largest Drawdown(%)':
                               largest_drawdown, 'Winner Percent(%)':winner_pct, 'YearlyRet/largestDD':yearret_largestDD, 
                                '99 Daily VAR(%)':var99daily, '95 Daily VAR(%)':var95daily}, 
                               index=['XAU_InSample','XAU_OutSample','JPY_InSample','JPY_OutSample'])
Performance_Stats['Annual Return(%)']=Performance_Stats['Annual Return(%)']*100
Performance_Stats['Annual Volatility(%)']=Performance_Stats['Annual Volatility(%)']*100
Performance_Stats['Winner Percent(%)']=Performance_Stats['Winner Percent(%)']*100
Performance_Stats['Largest Drawdown(%)']=Performance_Stats['Largest Drawdown(%)']*100


In [24]:
p1=figure(plot_height=300, x_axis_type="datetime",sizing_mode="scale_width",
         title='In-sample XAU strategy total return')
p1.line(source=XAU_InS*100,x='Date',y='Agg_QS_R_NoFrac',line_width=1,
       color='purple',legend='Total Return No Spread')
p1l2=p1.line(source=XAU_InS*100,x='Date',y='Agg_QS_R',line_width=2,
       color='red',legend='Total Return Spread')
p1l1=p1.line(source=100*XAU_InS/XAU_InS['Price'][0],x='Date',y='Price',line_width=0.5,
       color='blue',legend='Benchmark')
p1.legend.location='bottom_left'
p1.legend.click_policy="hide"
p1.add_tools(HoverTool(
    tooltips=[
        ( 'Date',   '@Date{%F}'            ),
        ( 'Benchmark',  '@Price{0.2f}' ), 
    ],

    formatters={
        'Date'      : 'datetime', 
    },
    mode='vline',
    renderers=[p1l1]
))
p1.add_tools(HoverTool(
    tooltips=[
        ( 'Date',   '@Date{%F}'            ),
        ( 'Total Return',  '@Agg_QS_R{0.2f}' ), 
    ],

    formatters={
        'Date'      : 'datetime', 
    },
    mode='vline',
    renderers=[p1l2]
))

p2=figure(plot_height=300, x_axis_type="datetime",sizing_mode="scale_width",title='Out-sample XAU strategy total return')
p2.line(source=XAU_OutS*100,x='Date',y='Agg_QS_R_NoFrac',line_width=1,
       color='purple',legend='Total Return No Spread')
p2l2=p2.line(source=XAU_OutS*100,x='Date',y='Agg_QS_R',line_width=2,
       color='red',legend='Total Return Spread')
p2l1=p2.line(source=100*XAU_OutS/XAU_OutS['Price'][0],x='Date',y='Price',line_width=0.5,
       color='blue',legend='Benchmark')
p2.legend.location='bottom_left'
p2.legend.click_policy="hide"
p2.add_tools(HoverTool(
    tooltips=[
        ( 'Date',   '@Date{%F}'            ),
        ( 'Benchmark',  '@Price{0.2f}' ), 
    ],

    formatters={
        'Date'      : 'datetime', # use 'datetime' formatter for 'date' field
    },
    mode='vline',
    renderers=[p2l1]
))
p2.add_tools(HoverTool(
    tooltips=[
        ( 'Date',   '@Date{%F}'            ),
        ( 'Total Return',  '@Agg_QS_R{0.2f}' ), 
    ],

    formatters={
        'Date'      : 'datetime', # use 'datetime' formatter for 'date' field
    },
    mode='vline',
    renderers=[p2l2]
))

p3=figure(plot_height=300, x_axis_type="datetime",sizing_mode="scale_width",title='In-sample JPY strategy total return')
p3.line(source=JPY_InS*100,x='Date',y='Agg_QS_R_NoFrac',line_width=1,
       color='purple',legend='Total Return No Spread')
p3l2=p3.line(source=JPY_InS*100,x='Date',y='Agg_QS_R',line_width=2,
       color='red',legend='Total Return Spread')
p3l1=p3.line(source=100*JPY_InS/JPY_InS['Price'][0],x='Date',y='Price',line_width=0.5,
       color='blue',legend='Benchmark')
p3.legend.location='bottom_left'
p3.legend.click_policy="hide"
p3.add_tools(HoverTool(
    tooltips=[
        ( 'Date',   '@Date{%F}'            ),
        ( 'Benchmark',  '@Price{0.2f}' ), 
    ],

    formatters={
        'Date'      : 'datetime', # use 'datetime' formatter for 'date' field
    },
    mode='vline',
    renderers=[p3l1]
))
p3.add_tools(HoverTool(
    tooltips=[
        ( 'Date',   '@Date{%F}'            ),
        ( 'Total Return',  '@Agg_QS_R{0.2f}' ), 
    ],

    formatters={
        'Date'      : 'datetime', # use 'datetime' formatter for 'date' field
    },
    mode='vline',
    renderers=[p3l2]
))


p4=figure(plot_height=300, x_axis_type="datetime",sizing_mode="scale_width",title='Out-sample JPY strategy total return')
p4.line(source=JPY_OutS*100,x='Date',y='Agg_QS_R_NoFrac',line_width=1,
       color='purple',legend='Total Return No Spread')
p4l2=p4.line(source=JPY_OutS*100,x='Date',y='Agg_QS_R',line_width=2,
       color='red',legend='Total Return Spread')
p4l1=p4.line(source=100*JPY_OutS/JPY_OutS['Price'][0],x='Date',y='Price',line_width=0.5,
       color='blue',legend='Benchmark')
p4.legend.location='bottom_right'
p4.legend.click_policy="hide"
p4.add_tools(HoverTool(
    tooltips=[
        ( 'Date',   '@Date{%F}'            ),
        ( 'Benchmark',  '@Price{0.2f}' ), 
    ],

    formatters={
        'Date'      : 'datetime', # use 'datetime' formatter for 'date' field
    },
    mode='vline',
    renderers=[p4l1]
))
p4.add_tools(HoverTool(
    tooltips=[
        ( 'Date',   '@Date{%F}'            ),
        ( 'Total Return',  '@Agg_QS_R{0.2f}' ), 
    ],

    formatters={
        'Date'      : 'datetime', # use 'datetime' formatter for 'date' field
    },
    mode='vline',
    renderers=[p4l2]
))

# make a grid
grid = gridplot([p1, p2,p3,p4], ncols=2, sizing_mode="scale_width", plot_height=500)

def update(spread=3):
    spd=spread/10000
    XAU_InS['QS_R']=XAU_InS['QS_R_NoFrac']-XAU_InS['Delta_Signal'].abs()*(1+XAU_InS['Return'])*spd/2
    XAU_InS['QS_R']=XAU_InS['QS_R'].fillna(0)
    XAU_InS['Agg_QS_R']=(XAU_InS['QS_R']+1).cumprod()
    
    XAU_OutS['QS_R']=XAU_OutS['QS_R_NoFrac']-XAU_OutS['Delta_Signal'].abs()*(1+XAU_OutS['Return'])*spd/2
    XAU_OutS['QS_R']=XAU_OutS['QS_R'].fillna(0)
    XAU_OutS['Agg_QS_R']=(XAU_OutS['QS_R']+1).cumprod()
    
    JPY_InS['QS_R']=JPY_InS['QS_R_NoFrac']-JPY_InS['Delta_Signal'].abs()*(1+JPY_InS['Return'])*spd/2
    JPY_InS['QS_R']=JPY_InS['QS_R'].fillna(0)
    JPY_InS['Agg_QS_R']=(JPY_InS['QS_R']+1).cumprod()
    
    JPY_OutS['QS_R']=JPY_OutS['QS_R_NoFrac']-JPY_OutS['Delta_Signal'].abs()*(1+JPY_OutS['Return'])*spd/2
    JPY_OutS['QS_R']=JPY_OutS['QS_R'].fillna(0)
    JPY_OutS['Agg_QS_R']=(JPY_OutS['QS_R']+1).cumprod()
    
    p1l2.data_source.data['Agg_QS_R'] = XAU_InS['Agg_QS_R'].values*100
    p2l2.data_source.data['Agg_QS_R'] = XAU_OutS['Agg_QS_R'].values*100
    p3l2.data_source.data['Agg_QS_R'] = JPY_InS['Agg_QS_R'].values*100
    p4l2.data_source.data['Agg_QS_R'] = JPY_OutS['Agg_QS_R'].values*100
    
    annual_ret = [] # annualized return
    annual_vol = [] # annualized volatility
    IR = []     # information ratio
    largest_drawdown = []   # largest drawdown
    yearret_largestDD = []  # yearly return/largest drawdown
    winner_pct = []      # winner percentage
    var99daily = []       # 99% hourly VAR
    var95daily = []       # 95% hourly VAR
    for i in range(4):
        annual_ret.append(pow(datalist[i]['Agg_QS_R'][-1], 255*24/datalist[i]['Agg_QS_R'].count()) - 1)
        annual_vol.append(datalist[i]['QS_R'].std()*np.sqrt(255*24))
        IR.append(annual_ret[i]/annual_vol[i])
        largest_drawdown.append((datalist[i]['Agg_QS_R'].cummax() - datalist[i]['Agg_QS_R']).max())
        winner_pct.append(datalist[i]['QS_R'][datalist[i]['QS_R'] > 0].count()/datalist[i]['QS_R'].count())
        yearret_largestDD.append(annual_ret[i]/largest_drawdown[i])
        daily_return = datalist[i].resample('d').last().dropna(subset=['Price'])
        var99daily.append(daily_return['QS_R'].quantile(.01)*100)
        var95daily.append(daily_return['QS_R'].quantile(.05)*100)
    
    Performance_Stats=pd.DataFrame({'Annual Return(%)':annual_ret, 'Annual Volatility(%)':annual_vol, 'InfoRatio':IR, 'Largest Drawdown(%)':
                                   largest_drawdown, 'Winner Percent(%)':winner_pct, 'YearlyRet/largestDD':yearret_largestDD, 
                                    '99 Daily VAR(%)':var99daily, '95 Daily VAR(%)':var95daily}, 
                                   index=['XAU_InSample','XAU_OutSample','JPY_InSample','JPY_OutSample'])
    Performance_Stats['Annual Return(%)']=Performance_Stats['Annual Return(%)']*100
    Performance_Stats['Annual Volatility(%)']=Performance_Stats['Annual Volatility(%)']*100
    Performance_Stats['Winner Percent(%)']=Performance_Stats['Winner Percent(%)']*100
    Performance_Stats['Largest Drawdown(%)']=Performance_Stats['Largest Drawdown(%)']*100
    print('Spread = ',spread,' base points: ')

    display(Performance_Stats)
    push_notebook()

# show the results
show(grid, notebook_handle=True)
interact_manual(update,spread=(0, 10, 0.5))
print('Spread = ',spd,' base points: ')
display(Performance_Stats)

interactive(children=(FloatSlider(value=3.0, description='spread', max=10.0, step=0.5), Button(description='Ru…

Spread =  0.0  base points: 


Annual Return(%)  Annual Volatility(%)  InfoRatio  \
XAU_InSample           7.588552              4.132387   1.836360   
XAU_OutSample          7.166453              5.834706   1.228246   
JPY_InSample           6.947270              6.146162   1.130343   
JPY_OutSample         18.130776              7.581750   2.391371   

               Largest Drawdown(%)  Winner Percent(%)  YearlyRet/largestDD  \
XAU_InSample              3.296470          47.792049             2.302023   
XAU_OutSample             2.517487          47.271838             2.846670   
JPY_InSample              3.258403          47.259440             2.132109   
JPY_OutSample             4.427971          47.624848             4.094601   

               99 Daily VAR(%)  95 Daily VAR(%)  
XAU_InSample         -0.112933        -0.052692  
XAU_OutSample        -0.126728        -0.057293  
JPY_InSample         -0.126539        -0.077162  
JPY_OutSample        -0.223647        -0.124492